# **Introduction to Large Language Models (LLMs)**

Large Language Models (LLMs) are advanced AI systems trained on huge amounts of data to understand and generate human-like language.  
Examples include **GPT**, **LLaMA**, **DeepSeek** and others.  

These models can:
- Answer questions  
- Summarize documents  
- Generate new text (code, stories, medical explanations, etc.)  
- Assist with research  

Traditionally, we use models hosted by companies (e.g., **ChatGPT from OpenAI** or **Claude from Anthropic**). While powerful, these have two drawbacks:
1. **Privacy concerns** → Your queries and files are sent to third-party servers.  
2. **Limited control** → You can’t customize the model itself.  

That’s where **open-source models** come in. With tools like **Ollama** and **Hugging Face**, we can run models ourselves.  
- **Ollama** makes it easy to run large models locally (or inside Colab).  
- **Hugging Face Transformers** provides thousands of models but requires more setup.  

In this notebook, we’ll:  
1. Install and run **Ollama** in Google Colab.  
2. Pull the **DeepSeek-R1** open-source model.  
3. Build a simple **interactive chatbot**.  
4. Discuss how you could also extend this to take files as input.  





In [ ]:
!pip uninstall -y langchain langchain-core langchain-community
!pip install langchain==0.1.17 langchain-core==0.1.52 langchain-community==0.0.36 chromadb==0.5.0 ipywidgets


Found existing installation: langchain 0.3.27
Uninstalling langchain-0.3.27:
  Successfully uninstalled langchain-0.3.27
Found existing installation: langchain-core 0.3.79
Uninstalling langchain-core-0.3.79:
  Successfully uninstalled langchain-core-0.3.79
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 5.6 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.3/67.3 kB 7.1 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 867.6/867.6 kB 20.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.9/302.9 kB 28.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 38.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 526.8/526.8 kB 45.2 MB/s eta 0

# 🚀 Setup: Installing Ollama in Google Colab

In [ ]:
# Install Ollama and required Python packages
!curl -fsSL https://ollama.com/install.sh | sh   # Download & install Ollama
!pip install ollama ipywidgets                  # Python client + widgets for UI
# !pip install transformers torch accelerate ipywidgets  # Optional Hugging Face libraries
!pip install sacremoses                         # Extra tokenizer package

# !pip uninstall -y langchain langchain-core langchain-community
# !pip install langchain==0.1.17 langchain-core==0.1.52 langchain-community==0.0.36 chromadb==0.5.0 ipywidgets




>>> Installing ollama to /usr/local
>>> Downloading Linux amd64 bundle
######################################################################## 100.0%
>>> Creating ollama user...
>>> Adding ollama user to video group...
>>> Adding current user to ollama group...
>>> Creating ollama systemd service...
>>> The Ollama API is now available at 127.0.0.1:11434.
>>> Install complete. Run "ollama" from the command line.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 897.5/897.5 kB 55.5 MB/s eta 0:00:00


**Here’s what’s happening:**

- `curl ... | sh` → downloads and installs Ollama on Colab.  
- `pip install ollama ipywidgets` → installs the Python interface for Ollama and widgets for interactive UI.  
- `pip install transformers torch accelerate` → installs Hugging Face’s core libraries (for an alternative way of running models).  
- `pip install sacremoses` → tokenizer helper needed by some Hugging Face models.  

---

# ▶️ Start the Ollama Service


In [ ]:
# Start Ollama in the background
!nohup ollama serve &  #no hang up, & tells the server to run this command in the background

nohup: appending output to 'nohup.out'


- `ollama serve` launches the Ollama background service that handles requests.  
- `nohup ... &` makes sure it keeps running in the background so our notebook can talk to it.  

---

# 📥 Pulling the Model

In [ ]:
# Pull desired model from Ollama
!ollama pull deepseek-r1:1.5b
!ollama pull nomic-embed-text

This downloads the **DeepSeek-R1** model from the Ollama registry.deepseek-r1:1.5b is the lightest model available (1.15B parameters). In order to download other models with higher parameters, you can refer to the url: https://ollama.com/library/deepseek-r1  

It’s an **open-source model**, so you’re not sending queries to third-party servers. Everything runs within Colab.  

---

# Python Setup

In [ ]:
import ollama
import ipywidgets as widgets
from IPython.display import display, clear_output

# Define which model we’ll use
MODEL_NAME = "deepseek-r1:1.5b"

print("✅ Setup complete!")
print("\n=== Loading the Model ===")

✅ Setup complete!

=== Loading the Model ===


In [ ]:
# The code below is downloading data from the given link
import gdown

file_url = 'https://drive.google.com/uc?id=16dxB5xtGlts4Yr-6DpQfY2d1SZM8lQ_H'
output_path='/content/clinical_data.txt' # Specify the output filename
gdown.download(file_url, output_path, quiet=False)

Downloading...
From: https://drive.google.com/uc?id=16dxB5xtGlts4Yr-6DpQfY2d1SZM8lQ_H
To: /content/clinical_data.txt
100%|██████████| 3.74k/3.74k [00:00<00:00, 14.4MB/s]


'/content/clinical_data.txt'

Here:
- `ollama` → Python client for talking to the Ollama server.  
- `ipywidgets` → allows us to create text boxes and buttons in Colab.  
- `display, clear_output` → control what’s shown on the screen.  
- `MODEL_NAME` → we specify `deepseek-r1:1.5B`.  

---

# 💬 Define a Function to interact with the Model

In [ ]:
def ask_biogpt(question):
    try:
        response = ollama.chat(
            model=MODEL_NAME,
            messages=[{'role': 'user', 'content': question}]
        )
        return response['message']['content']
    except Exception as e:
        return f"Error talking to Ollama: {str(e)}"

Explanation:
- `ollama.chat()` sends a message to the model.  
- We pass the conversation as a list of messages (`role: user, content: question`).  
- The model responds with `response['message']['content']`.  
- If anything goes wrong, we catch the error and print it.  

---

# 🎛 Interactive UI with Widgets


In [ ]:
# Input box for typing questions
input_box = widgets.Text(
    placeholder='Ask a biomedical question...',
    description='Question:',
    layout=widgets.Layout(width='80%')
)

# Output area where answers will appear
output_area = widgets.Output(layout=widgets.Layout(border='1px solid gray'))

# Button to submit
button = widgets.Button(description='Ask', button_style='success')

Here we’re creating:
- A text box for entering a question.  
- An output area with a border (to display the model’s answer).  
- A green “Ask” button.  

---

# ⚡ Add Button Logic


In [ ]:
def on_button_clicked(b):
    with output_area:
        clear_output()
        q = input_box.value.strip()
        if not q:
            print("Please enter a question.")
            return
        print(f"Question: {q}")
        ans = ask_biogpt(q)
        print(f"Answer: {ans}")

# Attach button click event
button.on_click(on_button_clicked)

# Display everything
display(input_box, button, output_area)


Text(value='', description='Question:', layout=Layout(width='80%'), placeholder='Ask a biomedical question...'…

Button(button_style='success', description='Ask', style=ButtonStyle())

Output(layout=Layout(border='1px solid gray'))

This function:
- Clears the old output.  
- Reads the text from the input box.  
- Sends the question to our `ask_biogpt()` function.  
- Prints both the question and the model’s answer.  

Finally, we display the input box, button, and output area.  

---

# 🛡 Why Open-Source Ollama vs ChatGPT?

- With **ChatGPT**, your queries are sent to OpenAI’s servers → privacy concerns for sensitive data (like medical or personal info).  
- With **Ollama**, the model runs locally (or in Colab) → your data stays with you.  
- Hugging Face also gives access to open-source models, but requires more manual setup. Ollama simplifies this.  

This makes Ollama a **safer and more customizable option**, especially in healthcare or research settings.  

---

---

# 📂 Extending: Inputting Files Instead of Just Text

So far we only typed text. But we could also extend this notebook to:
- Upload a **PDF, DOCX, or TXT file**.  
- Extract its text (using libraries like `pdfplumber` or `python-docx`).  
- Send that text into the LLM for summarization or question answering.  

That way, you could drop in a research paper and immediately start asking the model about it.  

We’ll use a **medical dataset example** consisting of 5 patients. Here, we will be training the llm on our custom dataset.

## 1️⃣ Install Required Packages

We need:

- `langchain-community` & `langchain-core`: for building LLM pipelines.
- `chromadb`: for storing embeddings in a vector database.
- `ipywidgets`: for interactive UI elements in Colab.
- `nomic-embed-text` : embedding model that converts text into a numerical vector

In [ ]:
# !pip uninstall -y langchain langchain-core langchain-community
# !pip install langchain==0.1.17 langchain-core==0.1.52 langchain-community==0.0.36 chromadb==0.5.0 ipywidgets
# !ollama pull nomic-embed-text

Found existing installation: langchain 0.1.17
Uninstalling langchain-0.1.17:
  Successfully uninstalled langchain-0.1.17
Found existing installation: langchain-core 0.1.52
Uninstalling langchain-core-0.1.52:
  Successfully uninstalled langchain-core-0.1.52
Found existing installation: langchain-community 0.0.36
Uninstalling langchain-community-0.0.36:
  Successfully uninstalled langchain-community-0.0.36
  Using cached langchain-0.1.17-py3-none-any.whl.metadata (13 kB)
  Using cached langchain_core-0.1.52-py3-none-any.whl.metadata (5.9 kB)
  Using cached langchain_community-0.0.36-py3-none-any.whl.metadata (8.7 kB)
Using cached langchain-0.1.17-py3-none-any.whl (867 kB)
Using cached langchain_core-0.1.52-py3-none-any.whl (302 kB)
Using cached langchain_community-0.0.36-py3-none-any.whl (2.0 MB)


## 2️⃣ Import Libraries

Here we import the necessary components for:

- LLM access
- Document loading
- Embeddings
- Vector database
- Text splitting
- Interactive widgets


What is LangChain?

LangChain is a framework designed to simplify the creation of applications that leverage Large Language Models (LLMs). It acts as an abstraction layer and a collection of tools that make it easy to chain together different components—like models, data sources, and other tools—to build more complex and powerful applications.

In [ ]:
from langchain_community.llms import Ollama
from langchain_community.document_loaders import TextLoader
from langchain_community.embeddings import OllamaEmbeddings
from langchain_community.vectorstores import Chroma
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain.chains import RetrievalQA
import ipywidgets as widgets
from IPython.display import display, clear_output

## 3️⃣ Load and Split Document

We split large documents into smaller **chunks** so the LLM can handle them without losing context.

- `chunk_size=512`: each chunk has 512 characters.
- `chunk_overlap=32`: keeps 32 characters overlapping between chunks to preserve context.

In [ ]:
# Load your document (replace with your path)
# Example path for a file in your Drive: '/content/drive/MyDrive/your_folder/your_document.txt'
loader = TextLoader('/content/clinical_data.txt')
docs = loader.load()

# Split into chunks
splitter = RecursiveCharacterTextSplitter(chunk_size=512, chunk_overlap=32)
chunks = splitter.split_documents(docs)

print(f"Document split into {len(chunks)} chunks")

Document split into 13 chunks


## 4️⃣ Generate Embeddings and Build Vector Store

- Convert chunks into **vector embeddings** (semantic representation).
- Store embeddings in **Chroma DB** for fast retrieval.

> Here, we use `nomic-embed-text`, an open-source embedding model.

In [ ]:
embeddings = OllamaEmbeddings(model="nomic-embed-text")
db = Chroma.from_documents(chunks, embeddings)

ERROR:chromadb.telemetry.product.posthog:Failed to send telemetry event ClientStartEvent: capture() takes 1 positional argument but 3 were given
ERROR:chromadb.telemetry.product.posthog:Failed to send telemetry event ClientCreateCollectionEvent: capture() takes 1 positional argument but 3 were given


## 5️⃣ Set Up Retrieval-Augmented QA Chain (RAG)

- The retriever searches for relevant document chunks.
- The LLM generates answers based on the retrieved chunks.

In [ ]:
# Retriever from vector store
retriever = db.as_retriever()

# Load Ollama LLM
llm = Ollama(model="deepseek-r1:1.5B")

# Build the QA chain
qa_chain = RetrievalQA.from_chain_type(
    llm=llm,
    retriever=retriever,
    return_source_documents=True,
)

## 6️⃣ Define Interactive Q&A Function

This function connects a text input box with the RAG pipeline.

In [ ]:
def ask_doc(question):
    result = qa_chain({"query": question})
    return result['result']

## 3️⃣ Load and Split Document

We split large documents into smaller **chunks** so the LLM can handle them without losing context.

- `chunk_size=512`: each chunk has 512 characters.
- `chunk_overlap=32`: keeps 32 characters overlapping between chunks to preserve context.


In [ ]:
# Load your document (replace with your path)
loader = TextLoader('/content/clinical_data.txt')
docs = loader.load()

# Split into chunks
splitter = RecursiveCharacterTextSplitter(chunk_size=512, chunk_overlap=32)
chunks = splitter.split_documents(docs)

print(f"Document split into {len(chunks)} chunks")


Document split into 13 chunks


In [ ]:
!ls /content/

clinical_data.txt  nohup.out  sample_data


## 4️⃣ Generate Embeddings and Build Vector Store

- Convert chunks into **vector embeddings** (semantic representation).
- Store embeddings in **Chroma DB** for fast retrieval.

> Here, we use `nomic-embed-text`, an open-source embedding model.


In [ ]:
embeddings = OllamaEmbeddings(model="nomic-embed-text")
db = Chroma.from_documents(chunks, embeddings)

ERROR:chromadb.telemetry.product.posthog:Failed to send telemetry event ClientStartEvent: capture() takes 1 positional argument but 3 were given
ERROR:chromadb.telemetry.product.posthog:Failed to send telemetry event ClientCreateCollectionEvent: capture() takes 1 positional argument but 3 were given


## 5️⃣ Set Up Retrieval-Augmented QA Chain (RAG)

- The retriever searches for relevant document chunks.
- The LLM generates answers based on the retrieved chunks.


In [ ]:
# Retriever from vector store
retriever = db.as_retriever()

# Load Ollama LLM
llm = Ollama(model="deepseek-r1:1.5B")

# Build the QA chain
qa_chain = RetrievalQA.from_chain_type(
    llm=llm,
    retriever=retriever,
    return_source_documents=True,
)


## 6️⃣ Define Interactive Q&A Function

This function connects a text input box with the RAG pipeline.


In [ ]:
def ask_doc(question):
    result = qa_chain({"query": question})
    return result['result']


## 7️⃣ Build Interactive Colab UI

We create:

- Text input box
- Submit button
- Output display area


In [ ]:
# Input box
query_box = widgets.Text(
    value='',
    placeholder='Type your query here...',
    description='Query:',
    layout=widgets.Layout(width='80%')
)

# Button to submit query
submit_button = widgets.Button(description="Ask")

# Output area
output = widgets.Output()


## 8️⃣ Handle Button Click

When the user clicks the "Ask" button:

1. Clear previous output.
2. Check if query is empty.
3. Run the query through the QA chain.
4. Display the answer.


In [ ]:
def on_submit(button):
    with output:
        clear_output()
        question = query_box.value
        if question.strip() == "":
            print("⚠️ Please enter a query.")
            return
        result = qa_chain({"query": question})
        print("✅ Answer:\n", result['result'])

submit_button.on_click(on_submit)

# Display everything in Colab
display(query_box, submit_button, output)


Text(value='', description='Query:', layout=Layout(width='80%'), placeholder='Type your query here...')

Button(description='Ask', style=ButtonStyle())

Output()

Sample Queries for the document:

*   Give me the details of Patient 1003
*   What are the vitals of the patient 1001
*   Can you tell me the demographics of Patient 1002

## ✅ Summary & Notes

- This notebook demonstrates **document-based QA** using **Ollama LLM** and **LangChain**.
- **Privacy**: Your document stays in Colab; no external server sees it.
- **Extensibility**:
  - Replace `TextLoader` with `PyPDFLoader` or `UnstructuredWordDocumentLoader` to load PDFs/DOCX.
  - Use other embeddings or LLMs if needed.
- **RAG** ensures the model answers using actual document content rather than only its pretrained knowledge.
